In [121]:
import os, sys
from pathlib import Path
import json
from collections import defaultdict

import webcolors
import colorsys

from plotly import tools
from plotly.offline import download_plotlyjs, init_notebook_mode, iplot
from plotly.graph_objs import Scatter, Scattergl, Figure, Layout, Scatter3d
init_notebook_mode()


DATA_DIR = Path("../data")
movie_paths = [movie for movie in DATA_DIR.iterdir() if DATA_DIR.is_dir() and movie.is_dir()]

movie_json = {}
for movie in movie_paths:
    movie_name = movie.parts[-1]
    json_path = Path(movie, movie_name + ".json")
    if json_path.exists():
        try:
            with json_path.open("r") as f:
                movie_json[movie_name] = json.load(f)
                f.close()
        except json.JSONDecodeError:
            print("Error decoding " + movie_name)


In [122]:
def rgb_color_format(hsv):
    #Brighten to beautify
    rgb = colorsys.hsv_to_rgb(hsv[0], hsv[1], hsv[2])
    return 'rgb(' + str(rgb[0] * 255) + ',' + str(rgb[1] * 255) + ',' + str(rgb[2] * 255) + ')'

def graph_color(movie_list, solo=False): 
    scatters = []
    #color_names = ['red', 'orangered', 'orange', 'gold', 'yellow', 'yellowgreen', 'green',
    #               'darkturquoise', 'blue', 'blueviolet', 'violet', 'mediumvioletred']
    
    first_movie = True
    for movie in movie_list:
        hues = []
        vals = []
        sizes = []
        colors = []
        texts = []
        for frame in movie_json[movie]:
            for color in frame["palette"]:
                hex_code = color["hex"][1:]
                color_area = color["area"]
                r = int('0x' + hex_code[0:2], 0) / 255
                g = int('0x' + hex_code[2:4], 0) / 255
                b = int('0x' + hex_code[4:6], 0) / 255
                hsv = colorsys.rgb_to_hsv(r, g, b)
                hues.append(hsv[0])
                vals.append(hsv[2])
                sizes.append(color_area * 1000)
                colors.append(rgb_color_format(hsv))
                texts.append(movie + "." + str(frame["framenumber"]) + ":" +
                             "{:.2f}".format(hsv[0]) + "," +
                             "{:.2f}".format(hsv[1]) + "," +
                             "{:.2f}".format(hsv[2]))
        if first_movie:
            visibility = True
            first_movie = False
        elif not solo:
            visibility = True
        else:
            visibility = "legendonly"
        scatters.append(Scattergl(x=hues,
                       y=vals,
                       mode='markers',
                       name=movie,
                       text=texts,
                       visible=visibility,
                       marker={
                        'color': colors,
                        'symbol': 'square',
                        'size': sizes,
                        'sizemode': 'area'
                       }
                       ))

    layout = Layout(xaxis={'title': 'Hue', 'showticklabels': False}, yaxis={'title': 'Value'})
    fig = Figure(data=scatters, layout=layout)
    iplot(fig)

In [135]:
#Single movie
#Click on the legend to add/remove additional movies to the view
graph_color([movie for movie in movie_json.keys()], solo=True)

In [124]:
#Action
movie_list = ['darkknight', 'otherguys', 'killbill1', 'watchmen', 'killbill2']
graph_color(movie_list)

In [125]:
#Comedy
movie_list = ['budapest', 'graduate', 'otherguys']
graph_color(movie_list)

In [126]:
#Drama
movie_list = ['budapest', 'fightclub', 'graduate', 'darkknight', 'jaws', 'mulholland', 'shawshank', 'magnolia']
graph_color(movie_list)

In [127]:
#2010s
movie_list = ['budapest', 'cabin', 'otherguys']
graph_color(movie_list)

In [128]:
#2000s
movie_list = ['darkknight', 'killbill1', 'killbill2', 'mulholland', 'pianist', 'sincity', 'watchmen']
graph_color(movie_list)

In [129]:
#1990s
movie_list = ['eyeswideshut', 'fightclub', 'groundhog', 'magnolia', 'shawshank']
graph_color(movie_list)

In [130]:
#1980s
movie_list = ['et']
graph_color(movie_list)

In [131]:
#1970s
movie_list = ['jaws']
graph_color(movie_list)

In [132]:
#1960s
movie_list = ['graduate']
graph_color(movie_list)

In [133]:
#1950s
movie_list = ['rearwindow', 'vertigo']
graph_color(movie_list)